In [1]:
import pickle
import os
import pandas as pd
import sys
from itertools import chain
from collections import Counter

In [2]:
!{sys.executable} -m pip install torch
!{sys.executable} -m pip install torch-scatter -f https://data.pyg.org/whl/torch-1.10.2+cu102.html
!{sys.executable} -m pip install torch-sparse -f https://data.pyg.org/whl/torch-1.10.2+cu102.html
!{sys.executable} -m pip install torch-geometric
!{sys.executable} -m pip install ray
!{sys.executable} -m pip install "ray[tune]"
!{sys.executable} -m pip install -Uqq ipdb

     |▎                               | 7.0 MB 30.3 MB/s eta 0:00:29

     |▌                               | 13.2 MB 30.3 MB/s eta 0:00:29

     |▊                               | 19.4 MB 30.3 MB/s eta 0:00:29

     |█                               | 25.5 MB 30.3 MB/s eta 0:00:29

     |█▏                              | 31.7 MB 30.3 MB/s eta 0:00:29

...

     |███████████████████████████████▌| 866.9 MB 145.8 MB/s eta 0:00:01

     |███████████████████████████████▊| 874.2 MB 145.8 MB/s eta 0:00:01

     |████████████████████████████████| 881.1 MB 145.8 MB/s eta 0:00:01

     |████████████████████████████████| 881.9 MB 7.5 kB/s              
Looking in links: https://data.pyg.org/whl/torch-1.10.2+cu102.html
     |████████████████████████████████| 8.0 MB 30.3 MB/s            
Looking in links: https://data.pyg.org/whl/torch-1.10.2+cu102.html
     |████████████████████████████████| 2.9 MB 367 kB/s            
     |████████████████████████████████| 370 kB 28.0 MB/s            
  Preparing metadata (setup.py) ... done
     |████████████████████████████████| 231 kB 106.8 MB/s            
     |████████████████████████████████| 41 kB 1.1 MB/s             
  Created wheel for torch-geometric: filename=torch_geometric-2.0.3-py3-none-any.whl size=581953 sha256=3fd94c3d405bee36d142d0117a15e68a9b57227fea746a0f3779830122ce465f
  Stored in directory: /home/ec2-user/.cache/pip/wheels/d2/48/63/193500a1360033fb617b90aede62d33ef14dc8e5f5c5f0972a
Successfully built torch-geometric
     |████████████████████████████████| 54.5 MB 129 kB/s            
     |██████████████

     |████████████████████████████████| 461 kB 110.9 MB/s            
  Attempting uninstall: filelock
    Found existing installation: filelock 3.0.12
    Uninstalling filelock-3.0.12:
      Successfully uninstalled filelock-3.0.12
  Attempting uninstall: protobuf
    Found existing installation: protobuf 3.15.2
    Uninstalling protobuf-3.15.2:
      Successfully uninstalled protobuf-3.15.2
     |████████████████████████████████| 125 kB 28.3 MB/s            


In [3]:
module_path = "/home/ec2-user/SageMaker/sb-rec-system"
if module_path not in sys.path:
    sys.path.append(module_path)

from algorithms.srgnn_benchmark.srgnn.model import *

In [4]:
from dataio.sessionloader.latency_writter import *
from dataio.predictions import PredictionsWriter
from algorithms.evaluation.utils import SimpleStopwatch
from algorithms.evaluation.metrics.coverage import Coverage
from algorithms.evaluation.metrics.popularity import Popularity
from algorithms.evaluation.metrics.accuracy import MRR, HitRate
from algorithms.evaluation.metrics.accuracy_multiple import Precision, Recall, MAP, NDCG

In [5]:
def test(loader, test_model, dataset, train_data, latencies_out_file, pred_out_file):
    test_model.eval()
    
    metrics = [NDCG(), MAP(), Precision(), Recall(), HitRate(), MRR()
    , Coverage(training_df=train_data)
    , Popularity(training_df=train_data)]
    
    predictions_writer = PredictionsWriter(outputfilename=pred_out_file, evaluation_n=20)
    latency_writer = LatencyWriter(latencies_out_file)
    
    prediction_sw = SimpleStopwatch()
    
    score_exp = []
    correct = 0
    for _, data in enumerate(loader):
        data.to('cpu') #initial cuda
        with torch.no_grad():
            prediction_sw.start()
            score = test_model(data)
            pred = score.max(dim=1)[1]
            label = data.y
            next_items = data.y_next
            
            prediction_sw.stop(0)

        correct += pred.eq(label).sum().item()

        sub_scores = score.topk(20)[1]
        sub_scores = sub_scores.cpu().detach().numpy()

        for ele in range(sub_scores.shape[0]):
            top_k_pred = sub_scores[ele]
            recommendations = pd.Series(0.0, top_k_pred)
            
            
            if isinstance(next_items[ele], int) == True:
                n_item = [next_items[ele]]
            else:
                n_item = next_items[ele]

            predictions_writer.appendline(recommendations, n_item)
            

            for metric in metrics:
                metric.add(recommendations, np.array(n_item))
                
    scores = []
    for metric in metrics:
        metric_name, score = metric.result()
        scores.append("%.4f" % score)
        print(metric_name, "%.4f" % score)
        
    predictions_writer.close()
    score_exp.append(scores)
        
        
    for (position, latency) in prediction_sw.get_prediction_latencies_in_micros():
        latency_writer.append_line(position, latency)
    latency_writer.close()
    
    mtr = ['NDCG@20, MAP@20, Precision@20, Recall@20, HitRate@20, MRR@20',' Coverage@20', 'Popularity@20' ]
    with open(f'results/{dataset}.csv', 'a+') as f:
        f.write(",".join(str(item) for item in mtr))
        f.write('\n')
        f.write(",".join(str(item) for item in scores))


In [6]:
#best config settings from hyper param search
yoochoose = {
    'l2_penalty': 1e-05, 
    'lr': 0.001, 
    'epochs': 10, 
    'batch_size': 1, 
    'hidden_dim': 100, 
    'step': 3, 
    'weight_decay': 0.1,
    'num_items': 37484 
}

In [8]:
#best config settings from hyper param search
diginetica = {
    'l2_penalty': 1e-05, 
    'lr': 0.001, 
    'epochs': 10, 
    'batch_size': 1, 
    'hidden_dim': 100, 
    'step': 3, 
    'weight_decay': 0.1,
    'num_items': 43098
}

In [34]:
postnl = {
  "batch_size": 1,
  "epochs": 10,
  "hidden_dim": 125,
  "l2_penalty": 1e-05,
  "lr": 0.0007160251445470053,
  "weight_decay": 0.1,
  "step": 3,
  'num_items': None
}

In [36]:
data_dir = '/home/ec2-user/SageMaker/sb-rec-system/data/prepared/srgnn/'
model_dir = '/home/ec2-user/SageMaker/sb-rec-system/algorithms/srgnn_benchmark/trained_models'

items = [463,488,522]
for slice in range(3):
    
    dataset = f'srgnn_postnl_{slice}'
    
    config = postnl
    nitems = items[slice]
    config.update({"num_items" : nitems})
    
    train_data = pickle.load(open(data_dir + f'item_views_tra_seqs.{slice}.txt', 'rb'))
    lst = list(chain(*train_data))
    train_data = pd.DataFrame (lst, columns = ['ItemId'])
    
    latencies_out_file = f'latencies/latencies_{dataset}.txt'
    pred_out_file = f'predictions/predictions_{dataset}.txt'
    
    test_dataset = GraphDataset(data_dir, f'item_views_test.{slice}')
    
    test_loader = pyg_data.DataLoader(test_dataset,
                             batch_size=config["batch_size"],
                             shuffle=False,
                             drop_last=False)

    
    best_model = SRGNN(config["hidden_dim"], config["num_items"])
    path = os.path.join(model_dir, f"srgnn_postnl_{slice}")
    best_model.load_state_dict(torch.load(path, map_location=torch.device('cpu')))
    test(test_loader, best_model, dataset, train_data, latencies_out_file, pred_out_file)

NDCG@20:  0.4682
MAP@20:  0.0455
Precision@20:  0.0771
Recall@20:  0.6711
HitRate@20:  0.7427
MRR@20:  0.3636
Coverage@20:  0.9719
Popularity@20:  0.2296
NDCG@20:  0.4088
MAP@20:  0.0399
Precision@20:  0.0674
Recall@20:  0.5923
HitRate@20:  0.6543
MRR@20:  0.3174
Coverage@20:  0.9815
Popularity@20:  0.2182
NDCG@20:  0.4249
MAP@20:  0.0414
Precision@20:  0.0694
Recall@20:  0.6301
HitRate@20:  0.7024
MRR@20:  0.3175
Coverage@20:  0.9501
Popularity@20:  0.0968


In [9]:
#model directory
dataset = 'yoochoose1_64'
model_dir = '/home/ec2-user/SageMaker/sb-rec-system/algorithms/srgnn_benchmark/trained_models'
data_dir = f'/home/ec2-user/SageMaker/sb-rec-system/algorithms/srgnn_benchmark/data/{dataset}'



#best hyper
config = yoochoose

train_data = pickle.load(open(data_dir + '/raw/all_train_seq.txt', 'rb'))
lst = list(chain(*train_data))
train_data = pd.DataFrame (lst, columns = ['ItemId'])


latencies_out_file = f'latencies/latencies_{dataset}.txt'
pred_out_file = f'predictions/predictions_{dataset}.txt'


test_dataset = GraphDataset(data_dir, 'test')


test_loader = pyg_data.DataLoader(test_dataset,
                             batch_size=config["batch_size"],
                             shuffle=False,
                             drop_last=False)


best_model = SRGNN(config["hidden_dim"], config["num_items"])
# path = os.path.join(model_dir, f"srgnn_{dataset}")
path = os.path.join(model_dir, f"srgnn_yoochoose1_64")
best_model.load_state_dict(torch.load(path))
test(test_loader, best_model, dataset,train_data, latencies_out_file, pred_out_file)

NDCG@20:  0.3449
MAP@20:  0.0352
Precision@20:  0.0854
Recall@20:  0.4629
HitRate@20:  0.6462
MRR@20:  0.2865
Coverage@20:  0.3154
Popularity@20:  0.1307


In [30]:
model = SRGNN(config["hidden_dim"], config["num_items"])
criterion = nn.CrossEntropyLoss()

optimizer = torch.optim.Adam(model.parameters(),
                             lr=config["lr"],
                             weight_decay=config["l2_penalty"])

scheduler = optim.lr_scheduler.StepLR(optimizer,
                                      step_size=config["step"],
                                      gamma=config["weight_decay"])


test_dataset = GraphDataset(data_dir, 'test')


test_loader = pyg_data.DataLoader(test_dataset,
                             batch_size=config["batch_size"],
                             shuffle=False,
                             drop_last=False)


path = os.path.join(model_dir, f"srgnn_yoochoose1_4_9")
checkpoint = torch.load(path)
optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
epoch = checkpoint['epoch']
loss = checkpoint['loss']

test(test_loader, model, dataset,train_data, latencies_out_file, pred_out_file)

NDCG@20:  0.0003
MAP@20:  0.0000
Precision@20:  0.0001
Recall@20:  0.0005
HitRate@20:  0.0004
MRR@20:  0.0001


In [15]:
#model directory
dataset = 'yoochoose1_4'
model_dir = '/home/ec2-user/SageMaker/sb-rec-system/algorithms/srgnn_benchmark/trained_models'
data_dir = f'/home/ec2-user/SageMaker/sb-rec-system/algorithms/srgnn_benchmark/data/{dataset}'



#best hyper
config = yoochoose

train_data = pickle.load(open(data_dir + '/raw/all_train_seq.txt', 'rb'))
# lst = list(chain(*train_data))
# train_data = pd.DataFrame (lst, columns = ['ItemId'])


In [18]:
len(set(list(chain(*train_data))))

30444